### Author: Rodolfo Elenes

Date Created: 8/5/2025

Purpose: To create the table full of players gamelogs that will be used for studies

Change log:
- 8/5/2025 - Initialized
- 9/22/2025 - Added Injury transformation functions

##### Imports

In [ ]:
import pandas as pd
import numpy as np
import duckdb
import time
from pathlib import Path
import warnings
import traceback
pd.set_option('display.max_columns', None)
warnings.filterwarnings("ignore")

In [ ]:
%run ./common_utils.ipynb

##### Create gamelog functions

In [ ]:
def create_player_gamelog_csv(con_memory, player_name, pfr_id):
#   Function name: create_player_gamelog_csv
#   Description: This function is used to generate a dataframe that contains a player's gamelog
#   Parameters: con_memory, player_name, pfr_id
#        con_memory(DuckDB object): Connect to DuckDB session
#        player_name(str): First and Last name of a player, ex: Saquon Barkley
#        pfr_id(str): Pro Football Reference id used in each players URL to retrieve all gamelog information
#   Return values: df, status
#        df(pandas dataframe): The final dataframe that will be exported as a csv file
#        status: Tells the parent function this function's run result
    
    status = ""
    
    # Pickup regular season data
    lst_nm_initial = player_name[0].capitalize()  # Get last name initial
    time.sleep(6) # to respect website scraping policies
    url = f"https://www.pro-football-reference.com/players/{lst_nm_initial}/{pfr_id}/gamelog/"
    try:
        df = build_career_gmlog_df(url)
    except Exception as e:
        df = pd.DataFrame() # Have to return a value for df for pd.read_html() failures
        print("\nError:", e)
        print(f"Please check: {url}")
        traceback.print_exc()
        return df, status
            
    # Add playoffs data if available
    try:
        playoffs_df = build_career_gmlog_df(url, playoffs=True)
        df = pd.concat([df, playoffs_df])
    except:
        pass
        
    try:
        df = df_rebuild(con_memory, df, player_name, pfr_id)
        total_rush_att = df['RushAtt'].sum()
        if total_rush_att <= 268:   # sets minimum rushing attempt requirement for players to be saved
            print(f"Insufficient gamelog data for {player_name}. Player has {total_rush_att} rushing attempts logged.")
            status = "Insufficient data"
        else:
            print(f"Gamelog for {player_name}")
            display(df)
            status = "Save"
    except Exception as e:
        print(f"Unsupported gamelog schema for {player_name}. Please check: {url}")
        print("\nError:", e, "\n")
        traceback.print_exc()
        return df, status

        
    return df, status

In [ ]:
def build_career_gmlog_df(url, playoffs=False):
#   Function name: build_career_gmlog_df
#   Description: This function is used to scrape the raw dataframe of the player's gamelog from pfr's website 
#   Parameters: url, playoffs
#        url(str): The URL that points to a player's gamelog
#        playoffs(boolean): Tells the function to extract the regular season or playoffs table
#   Return values: df, status
#        df(pandas dataframe): The raw dataframe that will be transformed into the final dataframe
    
    if playoffs == True:
        df = pd.read_html(url, header=[0, 1])[1]
    else:
        df = pd.read_html(url, header=[0, 1])[0]
        
    # Fill top-level header missing values forward
    cols = pd.DataFrame(df.columns.tolist())
    cols.iloc[:, 0] = cols.iloc[:, 0].replace("Unnamed:.*", pd.NA, regex=True).fillna(method='ffill')
    # Rebuild MultiIndex
    df.columns = pd.MultiIndex.from_frame(cols)
    df = df[['NaN', 'Rushing', 'Receiving', 'Snap Counts']]

    # Then flatten as before
    df.columns = [
        f"{a}_{b}".strip('_') if b else a 
        for a, b in df.columns
    ]

    if playoffs == True:
        df['Season_type'] = "POST"
    else:
        df['Season_type'] = "REG"
        
    df = df.loc[:, ~df.columns.duplicated()] # Drops duplicate columns
    
    return df

In [ ]:
def df_rebuild(con_memory, df, player_name, pfr_id):
#   Function name: df_rebuild
#   Description: This function is used to take the raw dataframe and apply all necessary transformations
#   Parameters: con_memory, df
#        con_memory(DuckDB object): Connect to DuckDB session
#        df(pandas dataframe): The raw input dataframe
#   Return values: df, status
#        df(pandas dataframe): The final dataframe that will be saved as a csv file

    # Remove nan_ from Date and GS, rename Gcar col
    new_cols = []
    for col in df.columns:
        if "nan" in col:
            if col == 'nan_Gcar':  # Exclusively rename Gcar to CarGm
                col = 'CarGm'
            new_cols.append(col.replace("nan_", ""))
        else:
            new_cols.append(col)
    df.columns = new_cols

    # Add columns that are low priority
    process_columns = ['CarGm', 'Date', 'GS', 'Season_type', 'Week', 'Team', 'Rushing_Att', 'Rushing_Yds', 'Rushing_TD', 'Receiving_Tgt', 'Receiving_Rec', 'Receiving_Yds', 'Receiving_TD', 'Snap Counts_OffSnp', 'Snap Counts_STSnp']
    for col in process_columns:
        if col not in ['Snap Counts_OffSnp', 'Snap Counts_STSnp']:
            continue
        if col not in df.columns:
            df[col] = 0
    df = df[process_columns]
    
    # filter out rows that do not contain games (i.e. header rows, summary rows, etc.)
    df['Date'] = pd.to_datetime(df['Date'], errors='coerce')
    df = df.dropna(subset=['Date']).reset_index(drop = True)
    
    # Create Season column
    min_year = (df['Date'].min().year) - 1  # subtracting for players who debutted in next calendar year
    max_year = df['Date'].max().year
    df['Season'] = ''
    for i in range(max_year, min_year - 1, -1):
        start_date = f"{i}-08-01"
        end_date = f"{i + 1}-03-01"
        date_filter = (df['Date'] > start_date) & (df['Date'] <= end_date)
        df["Season"] = np.where(date_filter, i, df["Season"])

    # Final column rename
    edit_df_cols = df.columns.tolist()
    final_columns = ['CarGm', 'Date', 'GS', 'Season_type', 'Week', 'Team', 'RushAtt', 'RushYds', 'RushTD', 'Tgt', 'Rec', 'RecYds', 'RecTD', 'OffSnp', 'STSnp', 'Season']
    for i in range(df.shape[1]):
        edit_df_cols[i] = final_columns[i]
    df.columns = edit_df_cols
    
    df['GS'] = np.where(df['GS'] == '*', 1, 0)  # make Game Started column binary
    df = apply_schema(df)
        
    # Final order
    df['Player'] = ''
    df['pfr_id'] = ''
    column_order = ['CarGm', 'Team', 'Player', 'pfr_id', 'Date', 'Season', 'Week', 'Season_type', 'GS', 'RushAtt', 'RushYds', 'RushTD', 
                    'Tgt', 'Rec', 'RecYds', 'RecTD', 'OffSnp', 'STSnp']
    df = df[column_order].sort_values("Date").reset_index(drop=True)
    df['CarGm'] = range(1, len(df) + 1) # Numerize the Career Games based off the Dates
    df = add_DNP_rows(df, player_name)
    df = trnsfrm_bye_weeks(df)
    df = add_DNP_dates(con_memory, df)
    df = trnsfrm_susp_weeks(df, player_name)
    df['Player'] = player_name
    df['pfr_id'] = pfr_id
    df = df[(df.Season != 2025)]
    df = trnsfrm_inj_weeks(df)
    df = infer_inj_weeks(df)
    
    return df

In [ ]:
def apply_schema(df):
#   Function name: apply_schema
#   Description: This function is used to apply the correct dataframe schema
#   Parameters: df
#        input_df(pandas dataframe): The input dataframe
#   Return values: df, status
#        df(pandas dataframe): The transformed dataframe with correct datatypes schema

    # apply proper schema
    int_cols = ['CarGm', 'Season', 'Week', 'GS', 'RushAtt', 'RushYds', 'RushTD', 'Tgt', 'Rec', 'RecYds', 'RecTD', 'OffSnp', 'STSnp']
    for col in int_cols:                
        if col not in ['CarGm', 'Season', 'Week', 'GS'] and df[col].isna().any():
            df[col] = df[col].fillna(0)
        df[col] = df[col].astype(float).astype(int)
    df['Date'] = pd.to_datetime(df['Date'], errors='coerce').dt.strftime('%Y-%m-%d')

    return df

##### DNP rows transformation functions

In [ ]:
def add_DNP_rows(input_df, player_name):
#   Function name: add_DNP_rows
#   Description: This function is used to add missing DNP rows to the dataframe
#   Parameters: input_df, player_name
#        input_df(pandas dataframe): The input dataframe
#        player_name(str): Name of the player
#   Return values: df
#        df(pandas dataframe): The transformed dataframe with DNP rows

    con_memory = duckdb.connect(database=':memory:')
    career_seasons = input_df['Season'].unique().tolist() # get the seasons in a list

    df_gamelog = input_df[(input_df['Season_type'] == 'REG')] # exclude playoffs rows
    df_playoffs = input_df[(input_df['Season_type'] == 'POST')] # store playoffs rows
    inpt_cols = input_df.columns
    df = pd.DataFrame(columns = inpt_cols)

    # split df_gamelog by seasons
    for season in career_seasons:
        df_season = df_gamelog[(df_gamelog['Season']) == season]
        if season >= 2021:
            week_games = list(range(1, 19))
        else:
            week_games = list(range(1, 18))

        df_DNP = pd.DataFrame(columns = inpt_cols)
        games_played = df_season['Week'].tolist()  # get weeks value from season
        weeks_missed = list(set(week_games) - set(games_played))  # get games missed

        #add DNP rows
        for week in weeks_missed:        
            df_DNP.loc[-1] = {'Week': week, 'Season_type': 'DNP', 'Season': season}  # Add DNP row
            df_DNP = df_DNP.reset_index(drop=True)

        df_season = pd.concat([df_season, df_DNP]).sort_values('Week').reset_index(drop=True)
        df_season['Team'] = df_season['Team'].ffill()  # fills DNP week with correct team
        if df_season['Team'].isna().any(): # in case forward fill doesnt work due to a player beginning the season injured
            df_season['Team'] = df_season['Team'].bfill()
        df_season = df_season.fillna(0)
        df = pd.concat([df, df_season])

    df = pd.concat([df, df_playoffs])
    df = df.sort_values(by = ['Season', 'Week']).reset_index(drop=True)
    
    # Add missing seasons
    df_sched = pd.read_csv(f"../tables/nfl_team_schedules/nfl_team_schedules.csv")
    df_roster = construct_df_roster(con_memory)
    df_roster = df_roster[(df_roster.Player == player_name)]

    gamelog_szns = df.Season.unique().tolist()
    roster_szns = df_roster.Season.unique().tolist()

    if gamelog_szns != roster_szns:
        missing_szns_chk = all(b - a == 1 for a, b in zip(gamelog_szns, gamelog_szns[1:]))
    else:
        missing_szns_chk = True

    if missing_szns_chk == False:
        missing_szns = list(set(roster_szns) - set(gamelog_szns))
        for year in missing_szns:
            if year >= 2021:
                week_games = list(range(1, 19))
            else:
                week_games = list(range(1, 18))

            df_temp = df[(df.Season == (year - 1))].reset_index(drop=True)
            df_temp2 = df_roster[(df_roster.Season == year)].reset_index(drop=True)

            df_mss_sched = df_sched[(df_sched.Team == df_temp2.iloc[0].loc['Team']) & (df_sched.Season == year)]   
            df_temp.loc[-1] = {'CarGm': 0, 'Date': df_mss_sched.Date.tolist(), 'Season': year, 'Season_type': 'DNP', 
                               'Team': df_temp2.iloc[0].loc['ABV'], 'Week': df_mss_sched.Week.tolist()}
            df_temp = df_temp.explode(['Date', 'Week'])
            df_temp = df_temp[(df_temp.Season == year) & (df_temp.Week.isin(week_games))].fillna(0)
            df = pd.concat([df, df_temp]).sort_values(by=['Season', 'Week']).reset_index(drop=True)
    
    df = apply_schema(df)
    con_memory.close()
    
    return df

In [ ]:
def trnsfrm_bye_weeks(df):
#   Function name: find_bye_weeks
#   Description: This function is used to correctly identify the bye weeks on DNP rows
#   Parameters: df
#        df(pandas dataframe): The input dataframe
#   Return values: df
#        df(pandas dataframe): The transformed dataframe with BYE week rows

    df_fltrd = df[(df["Season_type"] == 'DNP')]
    teams_played_for = df_fltrd['Team'].unique().tolist()
    years_played_for = df_fltrd['Season'].unique().tolist()

    df_teams = construct_df_teams()

    # Get all the bye weeks relevant to the player
    df_bye = pd.read_csv("../tables/bye_weeks_xref/bye_weeks_xref.csv")
    df_bye = pd.merge(df_bye, df_teams, on=['Team', 'PFR_ABV'], how='inner')
    df_bye = df_bye[df_bye.ABV.isin(teams_played_for)].reset_index(drop=True)
    df_bye = df_bye[df_bye.Season.isin(years_played_for)].reset_index(drop=True)
    df_bye = df_bye[['ABV', 'Season', 'Bye Week']]
    
    # Match the correct bye week to the players log on DNP rows
    merged_df = pd.merge(df_fltrd, df_bye, left_on=['Team', 'Season'], right_on=['ABV', 'Season'], how='inner')
    merged_df = merged_df[(merged_df["Week"] == merged_df["Bye Week"])]
    merged_df['Season_type'] = "BYE"
    merged_df = merged_df[df.columns].reset_index(drop=True)

    # Apply BYE week rows to the final df
    for row in range(merged_df.shape[0]):
        week_entry = merged_df.loc[row]
        season = week_entry.loc['Season']
        week = week_entry.loc['Week']
        index_row = df[(df['Season'] == season) & (df['Week'] == week)].index[0]
        df.loc[index_row] = week_entry
    
    
    return df

In [ ]:
def add_DNP_dates(con_memory, df):
#   Function name: add_DNP_dates
#   Description: Fill in correct dates for DNP rows
#   Parameters: con_memory, df
#        con_memory(DuckDB object): Connect to DuckDB session
#        df(pandas dataframe): The input dataframe
#   Return values: df
#        df(pandas dataframe): The transformed dataframe with filled out dates column

    df_sched = pd.read_csv("../tables/nfl_team_schedules/nfl_team_schedules.csv")
    df_DNP = df[(df["Season_type"] == 'DNP')]
    df_teams = construct_df_teams()

    df_sched = con_memory.execute(f"""SELECT df_sched.*, df_teams.ABV FROM df_sched 
                                 JOIN df_teams ON df_sched.Team = df_teams.Team""").fetchdf()

    df_DNP = con_memory.execute(f"""SELECT df_DNP.*, df_teams.Team as Team_Name FROM df_DNP 
                                 JOIN df_teams ON df_DNP.Team = df_teams.ABV""").fetchdf()

    df_DNP = con_memory.execute(f""" SELECT CarGm, df_sched.Date, df_DNP.* EXCLUDE (Team_Name, Date, CarGm)
                                 FROM df_sched JOIN df_DNP 
                                 ON df_sched.Team = df_DNP.Team_Name 
                                 AND df_sched.Season = df_DNP.Season AND df_sched.Week = df_DNP.Week 
                                 ORDER BY df_sched.Date""").fetchdf()
    
    df = df[(df['Season_type'] != 'DNP')]
    df = pd.concat([df, df_DNP]).sort_values(by=['Season', 'Week']).reset_index(drop=True)

    return df

In [14]:
def trnsfrm_susp_weeks(df, player_name):
#   Function name: trnsfrm_susp_weeks
#   Description: Transform DNP weeks into SUSP (suspended) rows based off the susp_weeks_xref.csv table
#   Parameters: df, player_name
#        df(pandas dataframe): The input dataframe
#        player_name(str): Name of the player
#   Return values: df
#        df(pandas dataframe): The transformed dataframe with target DNP rows transformed to SUSP

    szns_plyd = df.Season.unique().tolist()
    df_teams = construct_df_teams()
    df_susp = pd.read_csv("../tables/susp_weeks_xref.csv")
    df_susp = df_susp[(df_susp.Player == player_name) & (df_susp.Season.isin(szns_plyd))].reset_index(drop=True)

    for row in range(df_susp.shape[0]):
        susp_entry = df_susp.loc[row]
        if "game" in susp_entry.loc['Susp_len'].lower():      # For entries of x games suspensions
            susp_entry['Susp_len'] = int(susp_entry.Susp_len.split(" ")[0])
            susp_date = susp_entry.loc['Date']
            susp_len = susp_entry.loc['Susp_len']
            df_susp_dates = df[(df.Date >= susp_date) & (df["Season_type"] == 'DNP')]
            df_susp_dates = df_susp_dates.head(susp_len)
            df_susp_dates['Season_type'] = 'SUSP'
            idx_list = df_susp_dates.index.tolist()
            df.loc[idx_list] = df_susp_dates.loc[idx_list]
        else:                                                 # For entries of Entire xxxx Season suspensions
            susp_date = susp_entry.loc['Date']
            susp_szn = susp_entry.loc['Season']
            df_susp_dates = df[(df.Date >= susp_date) & (df["Season_type"] == 'DNP') & (df["Season"] == susp_szn)]
            df_susp_dates['Season_type'] = 'SUSP'
            idx_list = df_susp_dates.index.tolist()
            df.loc[idx_list] = df_susp_dates.loc[idx_list]
    df['SUSP'] = np.where((df.Season_type == 'SUSP'), 1, 0)

    return df

In [15]:
def trnsfrm_inj_weeks(df):
#   Function name: trnsfrm_inj_weeks
#   Description: Transform DNP weeks into INJ or INJ & SUSP based off df_inj
#   Parameters: df
#        df(pandas dataframe): The input dataframe
#   Return values: df
#        df(pandas dataframe): The transformed dataframe with target DNP + SUSP rows transformed to INJ or INJ & SUSP

    df['INJ'] = 0
    df_inj = pd.read_csv("../src/wkly_nfl_inj_reports.csv")
    df_inj['INJ'] = 1
    df_inj = df_inj[(df_inj.Position.isin(['RB', 'FB', 'HB']) & ~(df_inj['Game Status'].isnull()))][['Season', 'Week', 'Player', 'Game Status', 'Injuries']]
    df_merge = pd.merge(df, df_inj, on=['Season', 'Week', 'Player', 'Team'])
    if df_merge.shape[0] > 0:
        df2 = df_merge[(df_merge.Season_type.isin(['DNP', 'SUSP']))]
        inj_dates = df2.Date.tolist()
        df2['INJ'] = np.where(df2.Date.isin(inj_dates), 1, 0)
        df2['Season_type'] = np.where((df2.INJ == 1) & (df2.Season_type == 'DNP'), 'INJ', df2.Season_type)
        df2['Season_type'] = np.where((df2.INJ == 1) & (df2.SUSP == 1), 'INJ & SUSP', df2.Season_type)
        df = df[~(df.Date.isin(inj_dates))]
        df = pd.concat([df, df2]).sort_values(by=['Season', 'Week']).reset_index(drop=True)
    else:
        df['Game Status'] = np.nan
        df['Injuries'] = np.nan

    return df

In [38]:
def infer_inj_weeks(df):
#   Function name: infer_inj_weeks
#   Description: Fill DNP rows with INJ whereever its applicable
#   Parameters: df
#        df(pandas dataframe): The input dataframe
#   Return values: df
#        df(pandas dataframe): The transformed dataframe with inferred INJ weeks

    df_temp = df[(df.Season_type.isin(['DNP', 'BYE']))]
    seasons = df_temp.Season.unique().tolist()

    for year in seasons:
        df_temp2 = df_temp[(df_temp.Season == year)]
        dnp_weeks = df_temp2.Week.tolist()
        dnp_weeks.sort()

        inj_weeks = []
        big_injury = False
        for i in dnp_weeks:
            if i == dnp_weeks[-1]:
                continue
            subtract = dnp_weeks[dnp_weeks.index(i) + 1] - i # Compare first week in dnp_weeks list and the next one
            if subtract == 1:
                inj_weeks.append(dnp_weeks[dnp_weeks.index(i) + 1])
                inj_weeks.append(i)
            else:
                if big_injury == True:
                    df['Season_type'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks)) & (df.Season_type != 'BYE')), \
                                                     'INJ', df.Season_type)
                    df['INJ'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 1, df.INJ)
                    df['Game Status'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 'Out', df['Game Status'])
                    df['Injuries'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 'Inferred', df['Injuries'])
                    big_injury = False
                inj_weeks.clear()

            inj_weeks = sorted(list(set(inj_weeks)))
            if len(inj_weeks) >= 4: # Four DNP rows in a row will update DNP rows to INJ
                big_injury = True

        if big_injury == True:
            df['Season_type'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 'INJ', df.Season_type)
            df['INJ'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 1, df.INJ)
            df['Game Status'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 'Out', df['Game Status'])
            df['Injuries'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 'Inferred', df['Injuries'])
            
    return df

###### Main

In [41]:
def main():
#   Function name: main
#   Description: The entry function of the notebook

    con_memory = duckdb.connect(database=':memory:')
    print("All players that will have gamelog data scraped.")
    player_db = pd.read_csv("../tables/players_xref.csv")
    fltrd_player_db = player_db[player_db['gm_log_rtrvd'] == 0].reset_index(drop = True)
    player_count = 1
    display(fltrd_player_db)
    
    for row in range(player_db.shape[0]):
        player_entry = player_db.loc[row]
        player_name = player_entry.loc['Player']
        pfr_id = player_entry.loc['pfr_id']
        gm_log_rtrvd = player_entry.loc['gm_log_rtrvd']
        
        if gm_log_rtrvd == 0:
            print(f"Player ({player_count}/{fltrd_player_db.shape[0]}): {player_name}")
            df, status = create_player_gamelog_csv(con_memory, player_name, pfr_id)
            
            if status == "Save":
                gm_log_entry = 1 # Successful save
                save_df(df, "../tables/players_gamelogs/players", f"{player_name}_gamelog.csv")
            elif status == "Insufficient data":
                gm_log_entry = 2 # Insufficient data
            else:
                gm_log_entry = 3 # Failed save (lets me know to debug)
            
            player_db.loc[row, 'gm_log_rtrvd'] = gm_log_entry
            player_db.to_csv("../tables/players_xref.csv", index = False)
            print(f"Updated gm_log_rtrvd entry to {gm_log_entry} in players_ref.csv for {player_name}")
            player_count = player_count + 1
        else:
            continue

    print(f"Completed acquiring gamelog for {fltrd_player_db.shape[0]} players.")
    con_memory.close()
    
    if fltrd_player_db.shape[0] > 0:
        concatenate_all_files('players_gamelogs', 'players')
    
main()

All players that will have gamelog data scraped.


Team  ABV  Season Position          Player    pfr_id  \
0         Denver Broncos  DEN    1992       RB    Bob Perryman  PerrBo00   
1         Miami Dolphins  MIA    1993       RB  Bobby Humphrey  HumpBo00   
2    Pittsburgh Steelers  PIT    2024       RB    Boston Scott  ScotBo02   
3          New York Jets  NYJ    1995       RB     Brad Baxter  BaxtBr00   
4      Carolina Panthers  CAR    2009       RB     Brad Hoover  HoovBr00   
..                   ...  ...     ...      ...             ...       ...   
393  Pittsburgh Steelers  PIT    2009       RB   Willie Parker  ParkWi00   
394     Cleveland Browns  CLE    2013       RB  Willis McGahee  McGaWi00   
395        New York Jets  NYJ    2015       RB       Zac Stacy  StacZa00   
396       Dallas Cowboys  DAL    2007       RB   Zack Crockett  CrocZa00   
397   Cincinnati Bengals  CIN    2024       RB       Zack Moss  MossZa00   

     Birth_date  Age  Years_exp  Entry_year  Height  Weight  gm_log_rtrvd  
0    10/16/1964   27          5        1987      73     233             0  
1    10/11/1966   26          4        1989      73     201             0  
2     4/27/1995   28          6        2018      66     203             0  
3      5/5/1967   27          0        1995      73     235             0  
4    11/11/1976   32          9        2000      72     245             0  
..          ...  ...        ...         ...     ...     ...           ...  
393  11/11/1980   28          5        2004      70     209             0  
394  10/21/1981   31         10        2006      72     235             0  
395    4/9/1991   23          2        2013      69     224             0  
396   12/2/1972   34         12        1996      74     240             0  
397  12/15/1997   26          4        2020      70     215             0  

[398 rows x 13 columns]

Player (1/398): Bob Perryman
Gamelog for Bob Perryman


CarGm Team        Player    pfr_id        Date  Season  Week Season_type  \
0       1  NWE  Bob Perryman  PerrBo00  1987-09-13    1987     1         REG   
1       2  NWE  Bob Perryman  PerrBo00  1987-09-21    1987     2         REG   
2       0  NWE  Bob Perryman  PerrBo00  1987-10-04    1987     4         DNP   
3       0  NWE  Bob Perryman  PerrBo00  1987-10-11    1987     5         DNP   
4       0  NWE  Bob Perryman  PerrBo00  1987-10-18    1987     6         DNP   
..    ...  ...           ...       ...         ...     ...   ...         ...   
93      0  DEN  Bob Perryman  PerrBo00  1992-11-30    1992    13         INJ   
94      0  DEN  Bob Perryman  PerrBo00  1992-12-06    1992    14         INJ   
95      0  DEN  Bob Perryman  PerrBo00  1992-12-12    1992    15         INJ   
96      0  DEN  Bob Perryman  PerrBo00  1992-12-20    1992    16         INJ   
97      0  DEN  Bob Perryman  PerrBo00  1992-12-27    1992    17         INJ   

    GS  RushAtt  RushYds  RushTD  Tgt  Rec  RecYds  RecTD  OffSnp  STSnp  \
0    0        2        6       0    0    0       0      0       0      0   
1    0        0        0       0    0    0       0      0       0      0   
2    0        0        0       0    0    0       0      0       0      0   
3    0        0        0       0    0    0       0      0       0      0   
4    0        0        0       0    0    0       0      0       0      0   
..  ..      ...      ...     ...  ...  ...     ...    ...     ...    ...   
93   0        0        0       0    0    0       0      0       0      0   
94   0        0        0       0    0    0       0      0       0      0   
95   0        0        0       0    0    0       0      0       0      0   
96   0        0        0       0    0    0       0      0       0      0   
97   0        0        0       0    0    0       0      0       0      0   

    SUSP  INJ Game Status  Injuries  
0      0    0         nan       nan  
1      0    0         nan       nan  
2      0    0         nan       nan  
3      0    0         nan       nan  
4      0    0         nan       nan  
..   ...  ...         ...       ...  
93     0    1         Out  Inferred  
94     0    1         Out  Inferred  
95     0    1         Out  Inferred  
96     0    1         Out  Inferred  
97     0    1         Out  Inferred  

[98 rows x 22 columns]

Saving Bob Perryman_gamelog.csv at ../tables/players_gamelogs/players/Bob Perryman_gamelog.csv
Successfully saved Bob Perryman_gamelog.csv!
Updated gm_log_rtrvd entry to 1 in players_ref.csv for Bob Perryman
Player (2/398): Bobby Humphrey
Gamelog for Bobby Humphrey


...

Saving Zack Crockett_gamelog.csv at ../tables/players_gamelogs/players/Zack Crockett_gamelog.csv
Successfully saved Zack Crockett_gamelog.csv!
Updated gm_log_rtrvd entry to 1 in players_ref.csv for Zack Crockett
Player (398/398): Zack Moss
Gamelog for Zack Moss


CarGm Team     Player    pfr_id        Date  Season  Week Season_type  GS  \
0       1  BUF  Zack Moss  MossZa00  2020-09-13    2020     1         REG   0   
1       2  BUF  Zack Moss  MossZa00  2020-09-20    2020     2         REG   0   
2       0  BUF  Zack Moss  MossZa00  2020-09-27    2020     3         INJ   0   
3       0  BUF  Zack Moss  MossZa00  2020-10-04    2020     4         INJ   0   
4       0  BUF  Zack Moss  MossZa00  2020-10-13    2020     5         INJ   0   
..    ...  ...        ...       ...         ...     ...   ...         ...  ..   
86      0  CIN  Zack Moss  MossZa00  2024-12-09    2024    14         INJ   0   
87      0  CIN  Zack Moss  MossZa00  2024-12-15    2024    15         INJ   0   
88      0  CIN  Zack Moss  MossZa00  2024-12-22    2024    16         INJ   0   
89      0  CIN  Zack Moss  MossZa00  2024-12-28    2024    17         INJ   0   
90      0  CIN  Zack Moss  MossZa00  2025-01-04    2024    18         INJ   0   

    RushAtt  RushYds  RushTD  Tgt  Rec  RecYds  RecTD  OffSnp  STSnp  SUSP  \
0         9       11       0    4    3      16      1      39      0     0   
1         8       37       0    0    0       0      0      28      0     0   
2         0        0       0    0    0       0      0       0      0     0   
3         0        0       0    0    0       0      0       0      0     0   
4         0        0       0    0    0       0      0       0      0     0   
..      ...      ...     ...  ...  ...     ...    ...     ...    ...   ...   
86        0        0       0    0    0       0      0       0      0     0   
87        0        0       0    0    0       0      0       0      0     0   
88        0        0       0    0    0       0      0       0      0     0   
89        0        0       0    0    0       0      0       0      0     0   
90        0        0       0    0    0       0      0       0      0     0   

    INJ   Game Status  Injuries  
0     0           NaN       NaN  
1     0           NaN       NaN  
2     1           Out       Toe  
3     1  Questionable       Toe  
4     1  Questionable       Toe  
..  ...           ...       ...  
86    1           Out  Inferred  
87    1           Out  Inferred  
88    1           Out  Inferred  
89    1           Out  Inferred  
90    1           Out  Inferred  

[91 rows x 22 columns]

Saving Zack Moss_gamelog.csv at ../tables/players_gamelogs/players/Zack Moss_gamelog.csv
Successfully saved Zack Moss_gamelog.csv!
Updated gm_log_rtrvd entry to 1 in players_ref.csv for Zack Moss
Completed acquiring gamelog for 398 players.


CarGm Team       Player    pfr_id        Date  Season  Week Season_type  \
0       0  GNB  Aaron Jones  JoneAa00  2017-09-10    2017     1         DNP   
1       1  GNB  Aaron Jones  JoneAa00  2017-09-17    2017     2         REG   
2       2  GNB  Aaron Jones  JoneAa00  2017-09-24    2017     3         REG   
3       3  GNB  Aaron Jones  JoneAa00  2017-09-28    2017     4         REG   
4       4  GNB  Aaron Jones  JoneAa00  2017-10-08    2017     5         REG   
..    ...  ...          ...       ...         ...     ...   ...         ...   
86      0  CIN    Zack Moss  MossZa00  2024-12-09    2024    14         INJ   
87      0  CIN    Zack Moss  MossZa00  2024-12-15    2024    15         INJ   
88      0  CIN    Zack Moss  MossZa00  2024-12-22    2024    16         INJ   
89      0  CIN    Zack Moss  MossZa00  2024-12-28    2024    17         INJ   
90      0  CIN    Zack Moss  MossZa00  2025-01-04    2024    18         INJ   

    GS  RushAtt  RushYds  RushTD  Tgt  Rec  RecYds  RecTD  OffSnp  STSnp  \
0    0        0        0       0    0    0       0      0       0      0   
1    0        0        0       0    0    0       0      0       0      8   
2    0        0        0       0    0    0       0      0       0     12   
3    0       13       49       1    0    0       0      0      30      8   
4    1       19      125       1    1    1       9      0      53      0   
..  ..      ...      ...     ...  ...  ...     ...    ...     ...    ...   
86   0        0        0       0    0    0       0      0       0      0   
87   0        0        0       0    0    0       0      0       0      0   
88   0        0        0       0    0    0       0      0       0      0   
89   0        0        0       0    0    0       0      0       0      0   
90   0        0        0       0    0    0       0      0       0      0   

    SUSP  INJ Game Status  Injuries  
0      0    0         NaN       NaN  
1      0    0         NaN       NaN  
2      0    0         NaN       NaN  
3      0    0         NaN       NaN  
4      0    0         NaN       NaN  
..   ...  ...         ...       ...  
86     0    1         Out  Inferred  
87     0    1         Out  Inferred  
88     0    1         Out  Inferred  
89     0    1         Out  Inferred  
90     0    1         Out  Inferred  

[58537 rows x 22 columns]

Saving players_gamelogs.csv at ../tables/players_gamelogs/players_gamelogs.csv
Successfully saved players_gamelogs.csv!


In [39]:
# folder_location = f"../tables/players_gamelogs"
# directory_path = Path(folder_location + f"/players")
# file_paths = [entry for entry in directory_path.iterdir() if entry.is_file()]
# file_names = [file.name for file in file_paths]
# lst = []
# for i in file_names:
#     lst.append(i.split("_")[0])
    
# df = pd.read_csv("../tables/players_xref.csv")
# print(len(df[(df.gm_log_rtrvd == 0)].gm_log_rtrvd.tolist()))
# df['gm_log_rtrvd'] = np.where(df.Player.isin(lst), 0, df.gm_log_rtrvd)
# print(len(df[(df.gm_log_rtrvd == 0)].gm_log_rtrvd.tolist()))
# df.to_csv("../tables/players_xref.csv", index=False)
# df

339
442


Team  ABV  Season Position           Player    pfr_id  \
0          Detroit Lions  DET    2011       RB      Aaron Brown  BrowAa00   
1      Minnesota Vikings  MIN    2024       RB      Aaron Jones  JoneAa00   
2      Green Bay Packers  GNB    2017       RB  Aaron Ripkowski  RipkAa00   
3        Atlanta Falcons  ATL    2009       RB    Aaron Stecker  StecAa00   
4          New York Jets  NYJ    1992       RB         AB Brown  BrowAB00   
...                  ...  ...     ...      ...              ...       ...   
1237      Dallas Cowboys  DAL    2007       RB    Zack Crockett  CrocZa00   
1238  Cincinnati Bengals  CIN    2024       RB        Zack Moss  MossZa00   
1239      Miami Dolphins  MIA    2024       RB   Zander Horvath  HorvZa00   
1240     New York Giants  NYG    2024       RB  Tyrone Tracy Jr  TracTy00   
1241       New York Jets  NYJ    2022       RB   Zonovan Knight  KnigZo00   

      Birth_date  Age  Years_exp  Entry_year  Height  Weight  gm_log_rtrvd  
0     10/10/1985   25          2        2011      73     205             2  
1      12/2/1994   29          7        2017      69     208             0  
2     12/20/1992   24          2        2015      73     246             2  
3     11/13/1975   33         10        2000      70     213             0  
4      12/4/1965   26          3        1989      69     210             2  
...          ...  ...        ...         ...     ...     ...           ...  
1237   12/2/1972   34         12        1996      74     240             0  
1238  12/15/1997   26          4        2020      70     215             0  
1239  12/10/1998   25          2        2022      75     230             2  
1240  11/23/1999   24          0        2024      71     210             2  
1241   4/11/2001   20          0        2022      71     210             2  

[1242 rows x 13 columns]

In [ ]:
# df = pd.read_csv("C:/Users/Rodolfo/Jupyter_files/nfl_project/tables/players_gamelogs/players/Aaron Stecker_gamelog.csv")

# df_temp = df[(df.Season_type.isin(['DNP', 'BYE']))]
# seasons = df_temp.Season.unique().tolist()

# for year in seasons:
#     df_temp2 = df_temp[(df_temp.Season == year)]
#     dnp_weeks = df_temp2.Week.tolist()
#     dnp_weeks.sort()

#     inj_weeks = []
#     big_injury = False
#     for i in dnp_weeks:
#         if i == dnp_weeks[-1]:
#             continue
#         subtract = dnp_weeks[dnp_weeks.index(i) + 1] - i # Compare first week in dnp_weeks list and the next one
#         if subtract == 1:
#             inj_weeks.append(dnp_weeks[dnp_weeks.index(i) + 1])
#             inj_weeks.append(i)
#         else:
#             if big_injury == True:
#                 df['Season_type'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks)) & (df.Season_type != 'BYE')), \
#                                                  'INJ', df.Season_type)
#                 df['INJ'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 1, df.INJ)
#                 df['Game Status'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 'Out', df['Game Status'])
#                 df['Injuries'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 'Inferred', df['Injuries'])
#                 big_injury = False
#             inj_weeks.clear()

#         inj_weeks = sorted(list(set(inj_weeks)))
#         if len(inj_weeks) >= 4: # Four DNP rows in a row will update DNP rows to INJ
#             big_injury = True

#     if big_injury == True:
#         df['Season_type'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 'INJ', df.Season_type)
#         df['INJ'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 1, df.INJ)
#         df['Game Status'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 'Out', df['Game Status'])
#         df['Injuries'] = np.where(((df.Season == year) & (df.Week.isin(inj_weeks))), 'Inferred', df['Injuries'])
        
# display(df[(df.INJ == 1)])